In [118]:
import sys
stdout = sys.stdout
reload(sys)
sys.setdefaultencoding('utf-8')
sys.stdout = stdout


In [119]:
%matplotlib inline
# import sys
# reload(sys)
# sys.setdefaultencoding('utf8')
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import statsmodels.api as sm
import matplotlib.pyplot as plt
import scipy.stats as stats
import plotly
plotly.tools.set_credentials_file(username='prdpram08', api_key='vahwmX6mq11V2fHIeQi6')
import plotly.plotly as py
from plotly.graph_objs import *
import string
import plotly.graph_objs as go
import cufflinks as cf
import xlrd
# from sklearn.metrics import classification_report, confusion_matrix
# from sklearn.cross_validation import train_test_split
# from sklearn.linear_model import LassoLarsCV
# from sklearn.svm import SVC, LinearSVC
# from sklearn.ensemble import RandomForestClassifier
# from sklearn.neighbors import KNeighborsClassifier
# from sklearn.naive_bayes import GaussianNB
# from sklearn.linear_model import Perceptron
# from sklearn.linear_model import SGDClassifier
# from sklearn.tree import DecisionTreeClassifier
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.options.display.max_colwidth = 500
#df= pd.read_excel(open('C:\Users\pradeep.ram\Downloads\propsalanalysis\pr.xlsx','rb'), sheetname='Sheet1', encoding='ISO-8859-1')
#df= pd.read_excel(open('C:\Users\pradeep.ram\Downloads\propsalanalysis\pr.xlsx','rb'), sheetname='Sheet1', encoding='UTF-8')


In [120]:
import xlrd
file = 'data4.xlsx'
xls = xlrd.open_workbook(file)
l1=xls.sheet_names()
dfs=[]
for sheet_name in l1:
    df= pd.read_excel(open(file,'rb'), sheetname=sheet_name)
    df = df.iloc[:,1:3]
    df = df.iloc[10:]
    df.columns = ['Title', 'Description']
    df = df.reset_index(drop=True)
    for index, row in df.iterrows():
        if pd.isnull(row["Title"])==True:
            p=index
            break
    
    df = df.iloc[p+2:]    
    df.dropna(how='all',inplace=True)
    df.drop(df.tail(1).index,inplace=True)
    df.Description = df.Description.replace(np.nan, 'project', regex=True)
    df.Description=df.Description.astype(str)
    df.Title = df.Title.fillna(method='ffill')
    df["Count"]=1
    j=1
    for i in range(0,len(df)-1):
        if df.iloc[i,0]!=df.iloc[i+1,0]:
            df.iloc[i,2]=j
            j=j+1
        else:   
            df.iloc[i,2]=j
    dfg=df.groupby(['Count'])['Description'].apply(lambda x: ",".join(x)).reset_index()
    df = df.drop_duplicates(subset=['Count'])
    df.columns=["Title","Desc","Count"]
    df=pd.merge(df, dfg, on='Count')
    df.drop(['Desc','Count'], axis=1, inplace=True)
    df.iloc[0,1]='project'
    h=['Bidding Type','Client Address','Deadline','Description','Estimated Cost','Financier','Latest Update','Organisation','Project Location','Related Documents :','TI Ref. No.','Tender Notice No.']
    for index, row in df.iterrows():
        if (row["Description"]=="project") & (row["Title"] not in h):
            row["Description"]=row["Title"]
            row["Title"]="Project Title"
    df = df.set_index([df['Title'].eq('Project Title').cumsum(), 'Title'])['Description'].unstack().reset_index(drop=True)
    dfs.append(df)
    df=[]

data = pd.concat(dfs,axis=0)
data = data.reset_index(drop=True)

In [121]:
data1=data[["Project Title","Description","Organisation","Project Location","Deadline","Estimated Cost"]]
data1.head(10)

Title                                                                                                                                                                                                          Project Title  \
0                                                                                              1.Benin - Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant   
1                                2.Benin - Recruitment Of A Master Of Work For The Supervision And Control Of The Rehabilitation Works Of The Two Semi-collective Sanitation Systems Of Cité Nouvelle Vie And Cité Houéyiho1   
2                                                                                                                                         3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3      4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
4                                                                                                                                               5.Cape Verde - Elaboration Of The Strategic Plan Of "pro Empresa"- 2018-2021   
5                                                                                                                 6.Chad - Recruitment Of A (e) Consultant (e) National (e) Engineering Specialist In Rural Development Plan   
6                                                                  7.Congo Democratic Republic of - Acquisition, Implementation Of Interconnection Solutions, Optimization, Security And Supervision Of The Computer Network   
7                                                                                                                8.Egypt - Chemical Chamber Portal And Plastics Market Information System Business Model And Marketing Plan.   
8                                                                                                                           9.Ghana - Consultancy Service For It Service Management -iso 2000 Standard For Gnpcs It Services   
9                                                                                                                                      10.Kenya - Designing And Development Of Postal Corporation Of Kenya Official Website.   

Title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Description  \
0      Expression of Interest for Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant Is At Sème Podji,Description Assistance in the control of engineering for the rehabilitation of the Semi-Collective Sanitation Systems of the Cité Vie Nouvelle and 1 in Cotonou the assistance to the control of work for the realization of the Sludge Treatment Station East of SEME-PODJI,The missio ns are grouped in two (02) lots to have:,Lot1: Related s...   
1      Expression of Interest for Recruitment of a Master of Work for the Supervision and Control of the Rehabilitation Works of the Two Semi-Collective Sanitation Systems of Cité Nouvelle Vie and Cité Houéyiho1,Description The missions are grouped in two (02) lots namely:,Lot 1: Services related to the assistance to the prime contractor for the rehilitation of the Semi-Collective Sanitation Systems of the Cité Nouvelle Nouvelle and Houéyiho 1 & agrav e; Cotonou Lot2: Services related to the assist...   
2    

In [122]:
data1["DescriptionA"]=data1["Description"]

In [123]:
data1['DescriptionA'] = data1['DescriptionA'].str.replace(',', ' ')
# data1['DescriptionA'] = data1['DescriptionA'].str.replace('.', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace('-', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace('(', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace(')', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace(':', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace(';', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace('"', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace('/', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace('%', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace('&', ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace("'", ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.replace(".", ' ')
data1['DescriptionA'] = data1['DescriptionA'].str.lower()
data1.head()

Title                                                                                                                                                                                                          Project Title  \
0                                                                                              1.Benin - Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant   
1                                2.Benin - Recruitment Of A Master Of Work For The Supervision And Control Of The Rehabilitation Works Of The Two Semi-collective Sanitation Systems Of Cité Nouvelle Vie And Cité Houéyiho1   
2                                                                                                                                         3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3      4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
4                                                                                                                                               5.Cape Verde - Elaboration Of The Strategic Plan Of "pro Empresa"- 2018-2021   

Title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Description  \
0      Expression of Interest for Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant Is At Sème Podji,Description Assistance in the control of engineering for the rehabilitation of the Semi-Collective Sanitation Systems of the Cité Vie Nouvelle and 1 in Cotonou the assistance to the control of work for the realization of the Sludge Treatment Station East of SEME-PODJI,The missio ns are grouped in two (02) lots to have:,Lot1: Related s...   
1      Expression of Interest for Recruitment of a Master of Work for the Supervision and Control of the Rehabilitation Works of the Two Semi-Collective Sanitation Systems of Cité Nouvelle Vie and Cité Houéyiho1,Description The missions are grouped in two (02) lots namely:,Lot 1: Services related to the assistance to the prime contractor for the rehilitation of the Semi-Collective Sanitation Systems of the Cité Nouvelle Nouvelle and Houéyiho 1 & agrav e; Cotonou Lot2: Services related to the assist...   
2      Expression of Interest for Establishment of a Mining Sector Data Collection and Management System,Description Consultant Will Be Called to:,Evaluate the Needs of the Severe Data Collection and Management System; Design the Data Collection and Management System in Access Format; Train Users on the Data Collection and Management System; Facilitate a Validation Workshop of the Document of the Provisional Report; Produce an End of Mission Report.,Project ID: P149176,Procurement Method: Individua...   
3      Expression of Interest for Recruitment of a Design Office to Conduct a Technical, Economic and Environmental feasibility Study for the Establishment of Ten Market Platforms in the Framework of the Investment and Development Project for the Markets.,Project ID: P143417,Procurement Method: Selection Based On Consultant~s Qualification,Submission Deadline Date/Time: June 27, 2018 16:00,Language of Notice: French The consultant / design office will propose at least one team of experts with the f...   
4                                                                                                        

In [124]:
import nltk
# nltk.download('wordnet')
w_tokenizer = nltk.tokenize.WhitespaceTokenizer()
lemmatizer = nltk.stem.WordNetLemmatizer()

# def lemmatize_text(text):
#     return [lemmatizer.lemmatize(w,'v') for w in w_tokenizer.tokenize(text)]

from nltk.stem import PorterStemmer
porter = PorterStemmer()
def stem_text(text):
    return [porter.stem(w) for w in w_tokenizer.tokenize(text.decode('utf-8'))]

# i1['text_lemmatized'] = i1.Title.apply(lemmatize_text)
#df['text_lemmatized2'] = df.Title.apply(lemmatize_text)
data1['text_stem'] = data1["DescriptionA"].apply(stem_text)
data1.head()

Title                                                                                                                                                                                                          Project Title  \
0                                                                                              1.Benin - Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant   
1                                2.Benin - Recruitment Of A Master Of Work For The Supervision And Control Of The Rehabilitation Works Of The Two Semi-collective Sanitation Systems Of Cité Nouvelle Vie And Cité Houéyiho1   
2                                                                                                                                         3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3      4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
4                                                                                                                                               5.Cape Verde - Elaboration Of The Strategic Plan Of "pro Empresa"- 2018-2021   

Title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Description  \
0      Expression of Interest for Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant Is At Sème Podji,Description Assistance in the control of engineering for the rehabilitation of the Semi-Collective Sanitation Systems of the Cité Vie Nouvelle and 1 in Cotonou the assistance to the control of work for the realization of the Sludge Treatment Station East of SEME-PODJI,The missio ns are grouped in two (02) lots to have:,Lot1: Related s...   
1      Expression of Interest for Recruitment of a Master of Work for the Supervision and Control of the Rehabilitation Works of the Two Semi-Collective Sanitation Systems of Cité Nouvelle Vie and Cité Houéyiho1,Description The missions are grouped in two (02) lots namely:,Lot 1: Services related to the assistance to the prime contractor for the rehilitation of the Semi-Collective Sanitation Systems of the Cité Nouvelle Nouvelle and Houéyiho 1 & agrav e; Cotonou Lot2: Services related to the assist...   
2      Expression of Interest for Establishment of a Mining Sector Data Collection and Management System,Description Consultant Will Be Called to:,Evaluate the Needs of the Severe Data Collection and Management System; Design the Data Collection and Management System in Access Format; Train Users on the Data Collection and Management System; Facilitate a Validation Workshop of the Document of the Provisional Report; Produce an End of Mission Report.,Project ID: P149176,Procurement Method: Individua...   
3      Expression of Interest for Recruitment of a Design Office to Conduct a Technical, Economic and Environmental feasibility Study for the Establishment of Ten Market Platforms in the Framework of the Investment and Development Project for the Markets.,Project ID: P143417,Procurement Method: Selection Based On Consultant~s Qualification,Submission Deadline Date/Time: June 27, 2018 16:00,Language of Notice: French The consultant / design office will propose at least one team of experts with the f...   
4                                                                                                        

In [125]:
# import nltk
# # nltk.download('stopwords')
# from nltk.corpus import stopwords
# stop = stopwords.words('english')
# data1['text_stem']=data1['text_stem'].apply(lambda x: [item for item in x if item not in stop])
# data1.head()

In [126]:
# data1['text']=data1.text_new.apply(lambda x: ' '.join(x))

In [127]:
data1["BU"]=" "

In [128]:
enggword=['detail','prepar','road']
enggword1=['dpr','flyover']
enggword2=['dpr','by-pass']
enggword3=['locat','survey','digit','model']
enggword4=['project','manag','consult','hospit']
enggword5=['consult','road']
enggword6=['detail','report','bridg']
enggword7=['dpr','bridg']
enggword8=['dpr','road']
enggword9=['detail','report','flyover']
enggword10=['consult','structur']
enggword11=['consult','build']
enggword12=['consult','hous']
enggword13=['detail','report','survey']
enggword14=['develop', 'multimod', 'transit','hub']
enggword15=['detail','report','bu']
enggword16=['detail','prepar','lane']
enggword17=['consult','station']
enggword18=['consult','lane']
enggword19=['dpr','build']
enggword20=['prepar','draw','survey']
enggword21=['consult','architectur']
enggword22=['consult', 'prepar', 'zonal', 'develop', 'plan']
enggword23=['consult','landscap']
enggword24=['consult','packag']
enggword25=['consult','highway']
enggword26=['consult','bridg']
enggword27=["feasibl","studi","road"]
enggword28=['consult','terminu']
enggword29=['feasibl', 'studi','lane']
enggword30=['design', 'draw','road']
enggword31=['design', 'draw','lane']
enggword32=["studi","lane"]
enggword33=["consult","km"]
enggword34=["preliminari","km"]
enggword35=['consult','stand','bu']
enggword36=['consult','complex']
enggword37=['consult','develop','infrastructur']
enggword38=['consult','pmay']
enggword39=['consult','expressway']
enggword40=["studi","road"]
enggword41=["detail","report","complex"]
enggword42=["geolog","investig"]
enggword43=["consult","route"]
enggword44=["dpr","bu","stand"]
enggword45=["geotechn","studi"]
enggword46=["consult","bypass"]
enggword47=["geotechn","investig"]
enggword48=["topograph","survey"]
enggword49=["studi","build"]
railword=['detail','report','rail']
railword2=['detail','report','railway']
railword3=['consult','rail']
railword4=['consult','railway']
railword5=["studi","railway"]
railword6=["preliminari","railway"]
railword7=["studi","rail"]
railword8=["pmc","rail"]
railword9=["pmc","railway"]
railword10=['consult','side']
railword11=["design","draw","bridg"]
railword12=["estim","bridg"]
railword13=["consult","stn"]
railword14=["gad",'railway']
railword15=["plan",'railway']
bdword4=['consult','smart','citi']
# ttsword1=['detail','consult','smart','citi']
itsword1=['consult', 'automat', 'traffic','control']
itsword2=['master','system', 'integr']
itsword3=['integr','traffic']
itsword4=['traffic', 'signal']
itsword5=['instal', 'traffic']
itsword6=['integr','transport','system']
itsword7=['intellig','transport']
itsword8=['si','smart','citi']
itsword9=['traffic', 'control']
itsword10=['traffic', 'manag','system']
itsword=['repair','traffic','signal']
itword1=['ticket','bu','platform']
itword2=['implement','control','centr']
itword3=["vehicl","track"]
ttsword4=['consult','command','centr']
# ttsword6=['consult','smart','citi']
ttsword6=['consult','transport','implement']
# itword5=['system','integr']
ttsword5=['system','integr','consult','traffic']
itword6=['ict','master','plan']
ttsword7=['consult','cctv']
ttsword8=['consult','it']
itword8=['procur','gps']
itword9=['track','gps']
itword10=['intellig','transit']
itword11=['fare','system','collect']
erpword1=['erp','consult']
tpword1=['consult','transport']
tpword2=['consult','traffic']
tpword3=['consult','freight']
tpword4=['safeti','consult']
tpword5=['consult','multimod']
tpword6=["consult", "master","plan"]
tpword7=["consult", "mobil","plan"]
tpword8=["consult", "pedestrian"]
tpword9=["transport", "plan"]
tpword10=["urban", "plan"]
tpword11=["town", "plan"]
tpword12=["provis","transport","servic"]
tpword13=["region","plan"]
tpword14=["develop","road","plan"]
tpword15=["traffic","plan"]
tpword16=["develop","plan","prepar"]
tpword17=["integr","plan","develop"]
tpword18=["dpr","pedestrian"]
tpword19=["transport","studi"]
tpword20=["transport","document"]
tpword21=["traffic","impact"]
tpword22=['detail','report','freight']
tpword23=['master','plan']
tpword24=['road','safeti','audit']
tpword25=['socio','econom','impact']
tpword26=['transit','servic']
tpword27=['detail','report','town']
tpword28=['land','plan']
bpword1=["transact", "advisori"]
bpword2=["consult","car" "park"]
bpword3=["transact", "advisor"]
bpword4=["studi","car" "park"]
bpword5=["preliminari","car" "park"]
bpword6=["consult","ppp"]
bpword7=["fund","expert"]
bdword1=["transport","traffic","signal","transit",'route','bus']
bdword2=["monitor","project","consult"]
bdword3=["project","manag","consult"]

opword1=["implement", "park"]
opword2=["instal", "park"]
opword3=["manag", "bu","stand"]
opword4=["drive", "licens"]
rtword1=["consult", "bu"]
rtword2=['electr', 'buse' ]
rtword3=['electr', 'bu'] 
rtword4=['electr','vehicl']
stopword=['author','engin']
stopword2=['independ','engin']
stopword3=['authority', 'engin']
# stopword4=['supervis', 'consult', 'servic','lane']
stopword5=['consult','ae']
stopword6=['consult','ie']
stopword7=['dpr','lidar']
stopword8=['water','drainag']
stopword9=['system','integr','water']
stopword10=['water','expert']
stopword11=['water','suppli']
stopword12=['system','integr','child']
# stopword13=['system','integr','document']
stopword14=['satellit','track']
stopword15=['system','integr','secur']
stopword16=['shop','plan']
stopword17=['librari','academ','disabl','child','watershed','coal','drug','oil','fire','azur','insur','water','univers','lake','canal']

for index, row in data1.iterrows():
    m=row["text_stem"]
    if any(word in m  for word in bdword1):
        row["BU"]="BD2" 
    if all(word in m  for word in bdword2):
        row["BU"]="BD2" 
    if all(word in m  for word in bdword3):
        row["BU"]="BD2" 
    if all(word in m  for word in bdword4):
        row["BU"]="BD"  
    if all(word in m  for word in tpword3):
        row["BU"]="TP" 
    if all(word in m  for word in tpword5):
        row["BU"]="TP"
    if all(word in m  for word in tpword6):
        row["BU"]="TP" 
    if all(word in m  for word in tpword7):
        row["BU"]="TP"
    if all(word in m  for word in tpword8):
        row["BU"]="TP"
    if all(word in m  for word in tpword9):
        row["BU"]="TP" 
    if all(word in m  for word in tpword10):
        row["BU"]="TP"
    if all(word in m  for word in tpword11):
        row["BU"]="TP" 
    if all(word in m  for word in tpword12):
        row["BU"]="TP" 
    if all(word in m  for word in tpword13):
        row["BU"]="TP" 
    if all(word in m  for word in tpword14):
        row["BU"]="TP"
    if all(word in m  for word in tpword15):
        row["BU"]="TP" 
    if all(word in m  for word in tpword16):
        row["BU"]="TP"   
    if all(word in m  for word in tpword18):
        row["BU"]="TP" 
    if all(word in m  for word in tpword19):
        row["BU"]="TP" 
    if all(word in m  for word in tpword20):
        row["BU"]="TP"
    if all(word in m  for word in tpword21):
        row["BU"]="TP"  
    if all(word in m  for word in tpword22):
        row["BU"]="TP" 
    if all(word in m  for word in tpword23):
        row["BU"]="TP" 
    if all(word in m  for word in tpword24):
        row["BU"]="TP"  
    if all(word in m  for word in tpword25):
        row["BU"]="TP" 
    if all(word in m  for word in tpword26):
        row["BU"]="TP" 
    if all(word in m  for word in tpword27):
        row["BU"]="TP"
    if all(word in m  for word in tpword28):
        row["BU"]="TP"     
    if all(word in m  for word in rtword1):
        row["BU"]="RT" 
    if all(word in m  for word in rtword2):
        row["BU"]="RT" 
    if all(word in m  for word in rtword3):
        row["BU"]="RT" 
    if all(word in m  for word in rtword4):
        row["BU"]="RT"   
#     if all(word in m  for word in ttsword8 ):
#         row["BU"]="TTS"      
    if all(word in m  for word in enggword ):
        row["BU"]="Engg"
    if all(word in m  for word in enggword1 ):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword2 ):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword3 ):
        row["BU"]="Engg"     
    if all(word in m  for word in enggword4 ):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword5 ):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword6 ):
        row["BU"]="Engg"
    if all(word in m  for word in enggword7 ):
        row["BU"]="Engg"
    if all(word in m  for word in enggword8 ):
        row["BU"]="Engg"
    if all(word in m  for word in enggword9 ):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword10 ):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword11 ):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword12 ):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword13):
        row["BU"]="Engg"     
    if all(word in m  for word in enggword14):
        row["BU"]="Engg"
    if all(word in m  for word in enggword15):
        row["BU"]="Engg"
    if all(word in m  for word in enggword16):
        row["BU"]="Engg"   
    if all(word in m  for word in enggword17):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword18):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword19):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword20):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword21):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword22):
        row["BU"]="Engg"
    if all(word in m  for word in enggword23):
        row["BU"]="Engg"
#     if all(word in m  for word in enggword24):
#         row["BU"]="Engg"
    if all(word in m  for word in enggword25):
        row["BU"]="Engg"
    if all(word in m  for word in enggword26):
        row["BU"]="Engg"
    if all(word in m  for word in enggword27):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword28):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword29):
        row["BU"]="Engg"   
    if all(word in m  for word in enggword30):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword31):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword32):
        row["BU"]="Engg"
    if all(word in m  for word in enggword33):
        row["BU"]="Engg"
    if all(word in m  for word in enggword34):
        row["BU"]="Engg"
    if all(word in m  for word in enggword35):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword36):
        row["BU"]="Engg"
    if all(word in m  for word in enggword37):
        row["BU"]="Engg"
    if all(word in m  for word in enggword38):
        row["BU"]="Engg"
    if all(word in m  for word in enggword39):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword40):
        row["BU"]="Engg"
    if all(word in m  for word in enggword41):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword42):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword43):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword44):
        row["BU"]="Engg"  
    if all(word in m  for word in enggword45):
        row["BU"]="Engg"
    if all(word in m  for word in enggword46):
        row["BU"]="Engg"
    if all(word in m  for word in enggword47):
        row["BU"]="Engg"
    if all(word in m  for word in enggword48):
        row["BU"]="Engg" 
    if all(word in m  for word in enggword49):
        row["BU"]="Engg"     
    if all(word in m  for word in tpword2):
        row["BU"]="TP"    
    if all(word in m  for word in railword ):
        row["BU"]="Rail" 
    if all(word in m  for word in railword2 ):
        row["BU"]="Rail"  
    if all(word in m  for word in railword3 ):
        row["BU"]="Rail"    
    if all(word in m  for word in railword4 ):
        row["BU"]="Rail" 
    if all(word in m  for word in railword5 ):
        row["BU"]="Rail"  
    if all(word in m  for word in railword6 ):
        row["BU"]="Rail"  
    if all(word in m  for word in railword7 ):
        row["BU"]="Rail" 
    if all(word in m  for word in railword8 ):
        row["BU"]="Rail"
    if all(word in m  for word in railword9 ):
        row["BU"]="Rail" 
    if all(word in m  for word in railword10 ):
        row["BU"]="Rail"  
    if all(word in m  for word in railword11 ):
        row["BU"]="Rail" 
    if all(word in m  for word in railword12 ):
        row["BU"]="Rail"  
    if all(word in m  for word in railword13 ):
        row["BU"]="Rail"
    if all(word in m  for word in railword14):
        row["BU"]="Rail" 
    if all(word in m  for word in railword15):
        row["BU"]="Rail"     
    if all(word in m  for word in tpword4):
        row["BU"]="TP"     
#     if all(word in m  for word in ttsword1 ):
#         row["BU"]="TTS" 
    if all(word in m  for word in ttsword5 ):
        row["BU"]="TTS" 

    if all(word in m  for word in ttsword7 ):
        row["BU"]="TTS" 
#     if all(word in m  for word in ttsword2 ):
#         row["BU"]="TTS"     
    if all(word in m  for word in itsword1 ):
        row["BU"]="ITS"
    if all(word in m  for word in itsword2 ):
        row["BU"]="ITS" 
    if all(word in m  for word in itsword3 ):
        row["BU"]="ITS"
    if all(word in m  for word in itsword4 ):
        row["BU"]="ITS" 
    if all(word in m  for word in itsword5 ):
        row["BU"]="ITS" 
    if all(word in m  for word in itsword6 ):
        row["BU"]="ITS"
    if all(word in m  for word in itsword8 ):
        row["BU"]="ITS"
    if all(word in m  for word in itsword9 ):
        row["BU"]="ITS" 
    if all(word in m  for word in itsword10 ):
        row["BU"]="ITS"    
    if all(word in m  for word in itword10 ):
        row["BU"]="IT"   
    if all(word in m  for word in itword11 ):
        row["BU"]="IT"     
    if all(word in m  for word in itword1):
        row["BU"]="IT" 
    if all(word in m  for word in itword2):
        row["BU"]="IT"
    if all(word in m  for word in itword3):
        row["BU"]="IT" 
    if all(word in m  for word in ttsword4):
        row["BU"]="TTS"   
#     if all(word in m  for word in itword5):
#         row["BU"]="IT"
    if all(word in m  for word in itword6):
        row["BU"]="IT"   
    if all(word in m  for word in ttsword7):
        row["BU"]="TTS"     
    if all(word in m  for word in itsword7 ):
        row["BU"]="ITS"     
    if all(word in m  for word in tpword1):
        row["BU"]="TP"    
    if all(word in m  for word in erpword1):
        row["BU"]="TTS" 
    if all(word in m  for word in bpword2):
        row["BU"]="BP" 
    if all(word in m  for word in bpword4):
        row["BU"]="BP"
    if all(word in m  for word in bpword5):
        row["BU"]="BP" 
    if all(word in m  for word in bpword6):
        row["BU"]="BP"  
    if all(word in m  for word in bpword7):
        row["BU"]="BP"    
    if all(word in m  for word in opword1):
        row["BU"]="OP" 
    if all(word in m  for word in opword2):
        row["BU"]="OP"
    if all(word in m  for word in opword3):
        row["BU"]="OP" 
    if all(word in m  for word in opword4):
        row["BU"]="OP" 
    if all(word in m  for word in ttsword6 ):
        row["BU"]="TTS"    
#     if all(word in m  for word in stopword):
#         row["BU"]=" " 
#     if all(word in m  for word in stopword2):
#         row["BU"]=" " 
#     if all(word in m  for word in stopword3):
#         row["BU"]=" "  
#     if all(word in m  for word in stopword4):
#         row["BU"]=" " 
#     if all(word in m  for word in stopword5):
#         row["BU"]=" " 
#     if all(word in m  for word in stopword6):
#         row["BU"]=" " 
#     if all(word in m  for word in stopword7):
#         row["BU"]=" " 
    if all(word in m  for word in stopword8):
        row["BU"]=" " 
    if all(word in m  for word in stopword9):
        row["BU"]=" "
    if all(word in m  for word in stopword10):
        row["BU"]=" "
    if all(word in m  for word in stopword11):
        row["BU"]=" " 
#     if all(word in m  for word in stopword12):
#         row["BU"]=" "
#     if all(word in m  for word in stopword13):
#         row["BU"]=" " 
#     if all(word in m  for word in stopword14):
#         row["BU"]=" " 
#     if all(word in m  for word in stopword15):
#         row["BU"]=" "  
#     if all(word in m  for word in stopword16):
#         row["BU"]=" "
    if any(word in m  for word in stopword17):
        row["BU"]=" " 
    if all(word in m  for word in bpword3):
        row["BU"]="BP" 
    if all(word in m  for word in bpword1):
        row["BU"]="BP"      
# data1[["Project Title","Project Location","BU","Description","Estimated Cost","Organisation","text_stem"]]

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [153]:
# from nltk import PorterStemmer
PorterStemmer().stem('university')

u'univers'

In [130]:
data1["BD"]=" "
data1.head()

Title                                                                                                                                                                                                          Project Title  \
0                                                                                              1.Benin - Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant   
1                                2.Benin - Recruitment Of A Master Of Work For The Supervision And Control Of The Rehabilitation Works Of The Two Semi-collective Sanitation Systems Of Cité Nouvelle Vie And Cité Houéyiho1   
2                                                                                                                                         3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3      4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
4                                                                                                                                               5.Cape Verde - Elaboration Of The Strategic Plan Of "pro Empresa"- 2018-2021   

Title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Description  \
0      Expression of Interest for Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant Is At Sème Podji,Description Assistance in the control of engineering for the rehabilitation of the Semi-Collective Sanitation Systems of the Cité Vie Nouvelle and 1 in Cotonou the assistance to the control of work for the realization of the Sludge Treatment Station East of SEME-PODJI,The missio ns are grouped in two (02) lots to have:,Lot1: Related s...   
1      Expression of Interest for Recruitment of a Master of Work for the Supervision and Control of the Rehabilitation Works of the Two Semi-Collective Sanitation Systems of Cité Nouvelle Vie and Cité Houéyiho1,Description The missions are grouped in two (02) lots namely:,Lot 1: Services related to the assistance to the prime contractor for the rehilitation of the Semi-Collective Sanitation Systems of the Cité Nouvelle Nouvelle and Houéyiho 1 & agrav e; Cotonou Lot2: Services related to the assist...   
2      Expression of Interest for Establishment of a Mining Sector Data Collection and Management System,Description Consultant Will Be Called to:,Evaluate the Needs of the Severe Data Collection and Management System; Design the Data Collection and Management System in Access Format; Train Users on the Data Collection and Management System; Facilitate a Validation Workshop of the Document of the Provisional Report; Produce an End of Mission Report.,Project ID: P149176,Procurement Method: Individua...   
3      Expression of Interest for Recruitment of a Design Office to Conduct a Technical, Economic and Environmental feasibility Study for the Establishment of Ten Market Platforms in the Framework of the Investment and Development Project for the Markets.,Project ID: P143417,Procurement Method: Selection Based On Consultant~s Qualification,Submission Deadline Date/Time: June 27, 2018 16:00,Language of Notice: French The consultant / design office will propose at least one team of experts with the f...   
4                                                                                                        

In [131]:
bu1=['TP','OP']
bu2=['Rail','Engg','BP']
bu3=['IT','TTS']
bu4=['IT','ITS']
bu5=['RT']
bu6=['BD']
bu7=['BD2']
for index, row in data1.iterrows():
    m=row["BU"]
    if m in bu1:
        row['BD']='Ashish'   
    if m in bu2:
        row['BD']='Anand'      
    if m in bu3:
        row['BD']='Saumya' 
    if m in bu4:
        row['BD']='Gurpreet'  
    if m in bu5:
        row['BD']='Sudeep'  
    if m in bu6:
        row['BD']='All'
    if m in bu7:
        row['BD']='Check'     

In [132]:
data1['Estimated Cost'] = data1['Estimated Cost'].str.replace("INR,", 'Rs.')
data1.head()

Title                                                                                                                                                                                                          Project Title  \
0                                                                                              1.Benin - Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant   
1                                2.Benin - Recruitment Of A Master Of Work For The Supervision And Control Of The Rehabilitation Works Of The Two Semi-collective Sanitation Systems Of Cité Nouvelle Vie And Cité Houéyiho1   
2                                                                                                                                         3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3      4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
4                                                                                                                                               5.Cape Verde - Elaboration Of The Strategic Plan Of "pro Empresa"- 2018-2021   

Title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Description  \
0      Expression of Interest for Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant Is At Sème Podji,Description Assistance in the control of engineering for the rehabilitation of the Semi-Collective Sanitation Systems of the Cité Vie Nouvelle and 1 in Cotonou the assistance to the control of work for the realization of the Sludge Treatment Station East of SEME-PODJI,The missio ns are grouped in two (02) lots to have:,Lot1: Related s...   
1      Expression of Interest for Recruitment of a Master of Work for the Supervision and Control of the Rehabilitation Works of the Two Semi-Collective Sanitation Systems of Cité Nouvelle Vie and Cité Houéyiho1,Description The missions are grouped in two (02) lots namely:,Lot 1: Services related to the assistance to the prime contractor for the rehilitation of the Semi-Collective Sanitation Systems of the Cité Nouvelle Nouvelle and Houéyiho 1 & agrav e; Cotonou Lot2: Services related to the assist...   
2      Expression of Interest for Establishment of a Mining Sector Data Collection and Management System,Description Consultant Will Be Called to:,Evaluate the Needs of the Severe Data Collection and Management System; Design the Data Collection and Management System in Access Format; Train Users on the Data Collection and Management System; Facilitate a Validation Workshop of the Document of the Provisional Report; Produce an End of Mission Report.,Project ID: P149176,Procurement Method: Individua...   
3      Expression of Interest for Recruitment of a Design Office to Conduct a Technical, Economic and Environmental feasibility Study for the Establishment of Ten Market Platforms in the Framework of the Investment and Development Project for the Markets.,Project ID: P143417,Procurement Method: Selection Based On Consultant~s Qualification,Submission Deadline Date/Time: June 27, 2018 16:00,Language of Notice: French The consultant / design office will propose at least one team of experts with the f...   
4                                                                                                        

In [133]:
data1.dtypes

Title
Project Title       object
Description         object
Organisation        object
Project Location    object
Deadline            object
Estimated Cost      object
DescriptionA        object
text_stem           object
BU                  object
BD                  object
dtype: object

In [134]:
# data1['Deadline'] = pd.to_datetime(data1['Deadline'],format='%d%m%Y' )
data1['Deadline'] = pd.to_datetime(data1['Deadline'])
data1.head(500)

Title                                                                                                                                                                                                               Project Title  \
0                                                                                                   1.Benin - Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant   
1                                     2.Benin - Recruitment Of A Master Of Work For The Supervision And Control Of The Rehabilitation Works Of The Two Semi-collective Sanitation Systems Of Cité Nouvelle Vie And Cité Houéyiho1   
2                                                                                                                                              3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3           4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
4                                                                                                                                                    5.Cape Verde - Elaboration Of The Strategic Plan Of "pro Empresa"- 2018-2021   
5                                                                                                                      6.Chad - Recruitment Of A (e) Consultant (e) National (e) Engineering Specialist In Rural Development Plan   
6                                                                       7.Congo Democratic Republic of - Acquisition, Implementation Of Interconnection Solutions, Optimization, Security And Supervision Of The Computer Network   
7                                                                                                                     8.Egypt - Chemical Chamber Portal And Plastics Market Information System Business Model And Marketing Plan.   
8                                                                                                                                9.Ghana - Consultancy Service For It Service Management -iso 2000 Standard For Gnpcs It Services   
9                                                                                                                                           10.Kenya - Designing And Development Of Postal Corporation Of Kenya Official Website.   
10                                                                                                                                        11.Kenya - Feasibility Study Mapping Out Location Points For Installation Of Water Atms   
11                                           12.Kenya - Consultancy Services For Feasibility Study, Detailed Design And Preparation Of Tender Documents Of Two-rivers Dam And Expansion Of Sosiani Water Treatment Works Project.   
12                                                                                                                                                                                         13.Kenya - Provision Of Legal Services   
13                                                                                                                                                   14.Mauritius - Software Application For Aircraft Parking Allocation At Ssria   
14                                                                                                                                                 15.Morocco - Strengthening The Security Level Of The Radeec Information System   
15                                                                                                         16.Morocco - Development Of The Expertise Study Of The Building Located On The Right-of-way Of The Rn1 At Pk 122 + 200   
16          17.Morocco - Quality Control And Monitoring Services Of The Road Works In Four (04) Lots: Lot 0

In [135]:
data1["TenderScrutinyDate"]=pd.to_datetime("2018-06-18" )

In [136]:
data1.head()

Title                                                                                                                                                                                                          Project Title  \
0                                                                                              1.Benin - Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant   
1                                2.Benin - Recruitment Of A Master Of Work For The Supervision And Control Of The Rehabilitation Works Of The Two Semi-collective Sanitation Systems Of Cité Nouvelle Vie And Cité Houéyiho1   
2                                                                                                                                         3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3      4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
4                                                                                                                                               5.Cape Verde - Elaboration Of The Strategic Plan Of "pro Empresa"- 2018-2021   

Title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Description  \
0      Expression of Interest for Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant Is At Sème Podji,Description Assistance in the control of engineering for the rehabilitation of the Semi-Collective Sanitation Systems of the Cité Vie Nouvelle and 1 in Cotonou the assistance to the control of work for the realization of the Sludge Treatment Station East of SEME-PODJI,The missio ns are grouped in two (02) lots to have:,Lot1: Related s...   
1      Expression of Interest for Recruitment of a Master of Work for the Supervision and Control of the Rehabilitation Works of the Two Semi-Collective Sanitation Systems of Cité Nouvelle Vie and Cité Houéyiho1,Description The missions are grouped in two (02) lots namely:,Lot 1: Services related to the assistance to the prime contractor for the rehilitation of the Semi-Collective Sanitation Systems of the Cité Nouvelle Nouvelle and Houéyiho 1 & agrav e; Cotonou Lot2: Services related to the assist...   
2      Expression of Interest for Establishment of a Mining Sector Data Collection and Management System,Description Consultant Will Be Called to:,Evaluate the Needs of the Severe Data Collection and Management System; Design the Data Collection and Management System in Access Format; Train Users on the Data Collection and Management System; Facilitate a Validation Workshop of the Document of the Provisional Report; Produce an End of Mission Report.,Project ID: P149176,Procurement Method: Individua...   
3      Expression of Interest for Recruitment of a Design Office to Conduct a Technical, Economic and Environmental feasibility Study for the Establishment of Ten Market Platforms in the Framework of the Investment and Development Project for the Markets.,Project ID: P143417,Procurement Method: Selection Based On Consultant~s Qualification,Submission Deadline Date/Time: June 27, 2018 16:00,Language of Notice: French The consultant / design office will propose at least one team of experts with the f...   
4                                                                                                        

In [137]:
data1["DaysLeft"] = data1['Deadline'].sub(data1["TenderScrutinyDate"], axis=0)
data1.head(500)

Title                                                                                                                                                                                                               Project Title  \
0                                                                                                   1.Benin - Master Construction Recruitment For Supervision And Control Of Construction Works Of The New Sludge Treatment Plant   
1                                     2.Benin - Recruitment Of A Master Of Work For The Supervision And Control Of The Rehabilitation Works Of The Two Semi-collective Sanitation Systems Of Cité Nouvelle Vie And Cité Houéyiho1   
2                                                                                                                                              3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3           4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
4                                                                                                                                                    5.Cape Verde - Elaboration Of The Strategic Plan Of "pro Empresa"- 2018-2021   
5                                                                                                                      6.Chad - Recruitment Of A (e) Consultant (e) National (e) Engineering Specialist In Rural Development Plan   
6                                                                       7.Congo Democratic Republic of - Acquisition, Implementation Of Interconnection Solutions, Optimization, Security And Supervision Of The Computer Network   
7                                                                                                                     8.Egypt - Chemical Chamber Portal And Plastics Market Information System Business Model And Marketing Plan.   
8                                                                                                                                9.Ghana - Consultancy Service For It Service Management -iso 2000 Standard For Gnpcs It Services   
9                                                                                                                                           10.Kenya - Designing And Development Of Postal Corporation Of Kenya Official Website.   
10                                                                                                                                        11.Kenya - Feasibility Study Mapping Out Location Points For Installation Of Water Atms   
11                                           12.Kenya - Consultancy Services For Feasibility Study, Detailed Design And Preparation Of Tender Documents Of Two-rivers Dam And Expansion Of Sosiani Water Treatment Works Project.   
12                                                                                                                                                                                         13.Kenya - Provision Of Legal Services   
13                                                                                                                                                   14.Mauritius - Software Application For Aircraft Parking Allocation At Ssria   
14                                                                                                                                                 15.Morocco - Strengthening The Security Level Of The Radeec Information System   
15                                                                                                         16.Morocco - Development Of The Expertise Study Of The Building Located On The Right-of-way Of The Rn1 At Pk 122 + 200   
16          17.Morocco - Quality Control And Monitoring Services Of The Road Works In Four (04) Lots: Lot 0

In [138]:
columnsTitles=["Project Title","Description","Organisation","Project Location","Estimated Cost","BU","BD","Deadline","TenderScrutinyDate","DaysLeft"]
data1=data1.reindex(columns=columnsTitles)

In [139]:
data1[data1.BU != " "]

Title                                                                                                                                                                                                                    Project Title  \
2                                                                                                                                                   3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3                4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
5                                                                                                                           6.Chad - Recruitment Of A (e) Consultant (e) National (e) Engineering Specialist In Rural Development Plan   
11                                                12.Kenya - Consultancy Services For Feasibility Study, Detailed Design And Preparation Of Tender Documents Of Two-rivers Dam And Expansion Of Sosiani Water Treatment Works Project.   
15                                                                                                              16.Morocco - Development Of The Expertise Study Of The Building Located On The Right-of-way Of The Rn1 At Pk 122 + 200   
32                                                                  33.Rwanda,Uganda - Monitoring and Evaluation of Socio-economic Impact of the Project for the Rehabilitation and Widening of Kagitumba-kayonza-rusumo (208km) Road.   
42                                                                                                                                         43.Swaziland - Consultancy Services For A Property Development Project In Manzini, Eswatini   
43                                                            44.Tanzania - Consultant Services To Provide Technical Assistance To Project Management Team 0f Zanzibar Urban Services Project (mobility And Accessibility Coordinator)   
44                                                                                                                                             45.Tanzania - Technical Expert For The Development Of A Green Climate Fund Concept Note   
45                                                                                                                                          46.Uganda - Consultancy Services For Technical Audit Of Busega-mpigi Expressway (23.7 Km)’   
46                                                                                                                                                               47.Uganda - Preparation Of Physical Development Plans In The District   
52                                                 1.Afghanistan - Selection Of Preferred Technical Alternative And Preliminary Design For Upgrading The Torkham-jalalabad-kabul Highway Into A Multilane, Dual-carriageway Facilities   
54                                                                                                                            3.Azerbaijan - Consultant For Promoting The Role Of Civil Society In Gender Sensitive Sdg Implementation   
59                                                                       8.China - 2018 "strong Grasping" And "three Cities Lian Chuang" Small Street Alley, Traffic Junction Congestion Point And Flood Wa Point Renovation And Other   
68                                                                       17.China - Shuncheng District 2018 Traffic Infrastructure Construction Project (last Kilometer) Supervision Of New Reconstruction Project (two Announcements)   
72                                                                                                                 21.China - Bulletin Of Competitive Consultation On Construction Of Public Services In Gansu Expressway Service Area   
77                    

In [140]:
# from nltk import PorterStemmer
# PorterStemmer().stem('child')

In [141]:
data2 = data1[data1.BU != " "]
data2

Title                                                                                                                                                                                                                    Project Title  \
2                                                                                                                                                   3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
3                4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
5                                                                                                                           6.Chad - Recruitment Of A (e) Consultant (e) National (e) Engineering Specialist In Rural Development Plan   
11                                                12.Kenya - Consultancy Services For Feasibility Study, Detailed Design And Preparation Of Tender Documents Of Two-rivers Dam And Expansion Of Sosiani Water Treatment Works Project.   
15                                                                                                              16.Morocco - Development Of The Expertise Study Of The Building Located On The Right-of-way Of The Rn1 At Pk 122 + 200   
32                                                                  33.Rwanda,Uganda - Monitoring and Evaluation of Socio-economic Impact of the Project for the Rehabilitation and Widening of Kagitumba-kayonza-rusumo (208km) Road.   
42                                                                                                                                         43.Swaziland - Consultancy Services For A Property Development Project In Manzini, Eswatini   
43                                                            44.Tanzania - Consultant Services To Provide Technical Assistance To Project Management Team 0f Zanzibar Urban Services Project (mobility And Accessibility Coordinator)   
44                                                                                                                                             45.Tanzania - Technical Expert For The Development Of A Green Climate Fund Concept Note   
45                                                                                                                                          46.Uganda - Consultancy Services For Technical Audit Of Busega-mpigi Expressway (23.7 Km)’   
46                                                                                                                                                               47.Uganda - Preparation Of Physical Development Plans In The District   
52                                                 1.Afghanistan - Selection Of Preferred Technical Alternative And Preliminary Design For Upgrading The Torkham-jalalabad-kabul Highway Into A Multilane, Dual-carriageway Facilities   
54                                                                                                                            3.Azerbaijan - Consultant For Promoting The Role Of Civil Society In Gender Sensitive Sdg Implementation   
59                                                                       8.China - 2018 "strong Grasping" And "three Cities Lian Chuang" Small Street Alley, Traffic Junction Congestion Point And Flood Wa Point Renovation And Other   
68                                                                       17.China - Shuncheng District 2018 Traffic Infrastructure Construction Project (last Kilometer) Supervision Of New Reconstruction Project (two Announcements)   
72                                                                                                                 21.China - Bulletin Of Competitive Consultation On Construction Of Public Services In Gansu Expressway Service Area   
77                    

In [142]:
data2.sort_values(["Project Location","BU"], inplace=True)

In [143]:
data2

Title                                                                                                                                                                                                                    Project Title  \
52                                                 1.Afghanistan - Selection Of Preferred Technical Alternative And Preliminary Design For Upgrading The Torkham-jalalabad-kabul Highway Into A Multilane, Dual-carriageway Facilities   
834                                                                                                                                                 1.Afghanistan - Urban Planning And Development Services For Un Habitat Afghanistan   
1127                                                                                                                    1.Argentina - Consulting Service For The Strengthening Of The Public Integrity System And Information Analysis   
1123                                                                                                                                                            5.Australia - Supply And Delivery Of Traffic Signs And Control Devices   
597                                                                                            2.Austria - .net2018, Open Procedure For The Conclusion Of A Framework Agreement On The Provision Of .net Services For Ris Applications   
54                                                                                                                            3.Azerbaijan - Consultant For Promoting The Role Of Civil Society In Gender Sensitive Sdg Implementation   
837                                                                                                                                               4.Bangladesh - Purchase Of Procurer Nent And Instalation Of Vessel Traffic Managemen   
1333                                                                                                 3.Belarus - Correction And Support Of The Deployment Of Technical Means Of Traffic Management On The Street-road Network In Minsk   
1137                                      11.Brazil - Acquisition Of System And Equipment For The Ufba Card Project (or Ufbacard), According To The Conditions, Quantities, Requirements And Estimates Established In This Instrument.   
1348            18.Bulgaria - Removal Of Remarks From A General Overhaul Of A Bridge At Km 166 + 250 In The Kresna - Strumyani Interchange Between The 5th Sofia-kulata Main Railway Line And The Construction Of The Gauge Frames For   
2                                                                                                                                                   3.Burundi - Establishment Of A Mining Sector Data Collection And Management System   
841                                                                                                                 8.Cambodia - Consultant To Provide The External Relations (er) Activities To Build And Maintain The Profile Of Adb   
3                4.Cameroon - Recruitment Of A Design Office To Conduct A Technical, Economic And Environmental Feasibility Study For The Establishment Of Ten Market Platforms In The Framework Of The Investment And Development Pro   
468                                                                                                                                                                      15.Canada - Acquisition Of Signaling Superstructure (cacouna)   
1138                            12.Canada - Professional Engineering Services For The Completion Of A Traffic Study And The Pre-project Design For The Rehabilitation Of The Bougevard D~ange Gardien Nord (tronçon Turgeon-francoeur)   
1168                                                                                                                                                                                    42.Canada - Transit Fare Mobile Payment System   
1170                  

In [144]:
nreg=['Australia','Canada','Germany','Denmark','France','United States','Italy','Finland','Czech Republic','China','Belgium','Belarus','New Zealand']

In [145]:
# final=data2.loc[data2["Project Location"] != ['Australia','Canada','Germany','France','United States','Italy','Finland','Czech Republic','China','Belgium','Belarus']]
# final.drop(['text_stem','Project Title'], axis=1, inplace=True)
final=data2[~data2["Project Location"].isin(nreg)]

In [146]:
final = final.reset_index(drop=True)
final.head()

Title                                                                                                                                                                        Project Title  \
0      1.Afghanistan - Selection Of Preferred Technical Alternative And Preliminary Design For Upgrading The Torkham-jalalabad-kabul Highway Into A Multilane, Dual-carriageway Facilities   
1                                                                                                       1.Afghanistan - Urban Planning And Development Services For Un Habitat Afghanistan   
2                                                                           1.Argentina - Consulting Service For The Strengthening Of The Public Integrity System And Information Analysis   
3                                                  2.Austria - .net2018, Open Procedure For The Conclusion Of A Framework Agreement On The Provision Of .net Services For Ris Applications   
4                                                                                 3.Azerbaijan - Consultant For Promoting The Role Of Civil Society In Gender Sensitive Sdg Implementation   

Title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Description  \
0      Expression of Interest for Selection Of Preferred Technical Alternative And Preliminary Design For Upgrading The Torkham-jalalabad-kabul Highway Into A Multilane, Dual-carriageway Facilities,Description,This assignment has two major pa rts:,Phase I: A detailed study and analysis of alternative options/routes toidentify and recommend the P referred Alternative option for upgrading the entire length of Torkham-Jalalabad-Kabul highway into amulti-lane, dual-carriageway f acility. The proposed a...   
1                                                                                                                                                                                                                                                                                                                                                                                                                               Tenders are invited for Urban Planning and Development services for UN Habitat Afghanistan   
2      Expression of Interest for Consulting Service for the Strengthening of the Public Integrity System and Information Analysis of the Oa,Consulting Services, which include: Design, develop and produce pedagogical and audiovisual material to teach training courses and work training with a segmented strategy based on the tasks and responsibilities of public officials, in a broad sense. Design, develop and produce dissemination material to be used public encampments that install in society the iss...   
3                                                              Contract notice: .Net2018, open procedure for the conclusion of a framework agreement on the provision of .Net services for ris applications,The subject of the tender is the provision of .Net services by project managers, architecture consultants, developers and testers in the context of individual orders.,This contract is divided into lots: no,Time limit for receipt of tenders or requests to participate: date: 26/07/2018 Local time: 10:00   
4      Tenders are invited for Consultant for preparing the terms and conditions of the Call for Proposals, review and elaboration of the proposals, responding to the questions and providing feedback to the applicants in finalizing their full proposals.,Description,- Objective of the assignment The project w

In [147]:
data4 = data1[data1.BU == " "]
data4.sort_values(["Project Location","BU"], inplace=True)
final2=data4
# final2.drop(['text_stem','Project Title'], axis=1, inplace=True)
final2=data4[~data4["Project Location"].isin(nreg)]
final2 = final2.reset_index(drop=True)


In [148]:
dataA = final[final.BD == "Ashish"].reset_index(drop=True)
dataS = final[final.BD == "Saumya"].reset_index(drop=True)
dataG = final[final.BD == "Gurpreet"].reset_index(drop=True)
dataP = final[final.BD == "Sudeep"].reset_index(drop=True)
dataK = final[final.BD == "Anand"].reset_index(drop=True)
dataB=  final[final.BD == "All"].reset_index(drop=True)
dataC=  final[final.BD == "Check"].reset_index(drop=True)

In [149]:
from pandas import ExcelWriter
writer = ExcelWriter('OppurtinityList.xlsx')
final.to_excel(writer,'Oppurtunity')
final2.to_excel(writer,'Not_Oppurtinity')
dataA.to_excel(writer,'Ashish')
dataS.to_excel(writer,'Saumya')
dataG.to_excel(writer,'Gurpreet')
dataP.to_excel(writer,'Sudeep')
dataK.to_excel(writer,'Anand')
dataB.to_excel(writer,'All')
dataC.to_excel(writer,'Check')
writer.save()

In [150]:
# from pandas import ExcelWriter
# writer = ExcelWriter('OppurtinityList.xlsx')
# final.to_excel(writer,'Oppurtunity')
# final2.to_excel(writer,'Not_Oppurtinity')
# writer.save()